<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#SQL--dump" data-toc-modified-id="SQL--dump-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>SQL  dump</a></span><ul class="toc-item"><li><ul class="toc-item"><li><span><a href="#tutorials--used" data-toc-modified-id="tutorials--used-1.0.1"><span class="toc-item-num">1.0.1&nbsp;&nbsp;</span>tutorials  used</a></span></li></ul></li></ul></li><li><span><a href="#Even-wat-textmining" data-toc-modified-id="Even-wat-textmining-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Even wat textmining</a></span></li></ul></div>

# SQL  dump

* We show how to read in an sql dump using sqlite and then import it  into pandas
* We had to delete some commands from the sql dump and make it as simple as possible.

### tutorials  used

* <http://sebastianraschka.com/Articles/2014_sqlite_in_python_tutorial.html>
* <http://pythoncentral.io/introduction-to-sqlite-in-python/> and <http://pythoncentral.io/advanced-sqlite-usage-in-python/>




In [1]:
import sqlite3

In [2]:
# Create a database in RAM
db = sqlite3.connect(':memory:')
# Creates or opens a file called mydb with a SQLite3 DB
db = sqlite3.connect('data/mydb')
# Get a cursor object
cursor = db.cursor()

In [3]:
# try something out


cursor.execute('''
    CREATE TABLE users(id INTEGER PRIMARY KEY, name TEXT,
                       phone TEXT, email TEXT unique, password TEXT)
''')
db.commit()


In [4]:
cursor.execute('''DROP TABLE users''')
db.commit()

In [5]:
# read in a sql dump with one table

dump='/Users/admin/Documents/projects/Nederlab2016/DeCoster/decosterneol_tryout.sql'

!head -40 $dump


-- phpMyAdmin SQL Dump
-- version 4.0.10.17
-- https://www.phpmyadmin.net
--
-- Host: mysql12.meertens.knaw.nl
-- Generation Time: Jan 31, 2017 at 01:46 PM
-- Server version: 5.5.52-MariaDB
-- PHP Version: 5.3.3

-- SET SQL_MODE = "NO_AUTO_VALUE_ON_ZERO";
-- SET time_zone = "+00:00";


/*!40101 SET @OLD_CHARACTER_SET_CLIENT=@@CHARACTER_SET_CLIENT */;
/*!40101 SET @OLD_CHARACTER_SET_RESULTS=@@CHARACTER_SET_RESULTS */;
/*!40101 SET @OLD_COLLATION_CONNECTION=@@COLLATION_CONNECTION */;
/*!40101 SET NAMES utf8 */;

--
-- Database: `etymologie`
--

-- --------------------------------------------------------

--
-- Table structure for table `decosterneol`
--

CREATE TABLE IF NOT EXISTS `decosterneol` (
  `id` smallint(6) NOT NULL,
  `ingang` varchar(50) NOT NULL,
  `lemmatekst` text CHARACTER   NOT NULL
); 

--
-- Dumping data for table `decosterneol`
--

INSERT INTO `decosterneol` (`id`, `ingang`, `lemmatekst`) VALUES
(2, 'aaibaarheidsfactor', '<P><B>aaibaarheidsfactor,</B> schertsende benam

In [6]:
# put the data in the database
fd = open(dump, 'r')
script = fd.read()
cursor.executescript(script)
fd.close()

In [7]:
# take the data out

cursor.execute('''SELECT `ingang`, `lemmatekst`  FROM decosterneol''')
#user1 = cursor.fetchone() #retrieve the first row
#print(user1) #Print the first column retrieved(user's name)
all_rows = cursor.fetchall()

all_rows[:2] 

[('aaibaarheidsfactor',
  '<P><B>aaibaarheidsfactor,</B> schertsende benaming voor de mate van genoegen ondervonden door het aaien, knuffelen of vleien van bepaalde huisdieren (vooral katten), en bij uitbreiding ook mensen en dingen. Een alligator heeft een erg lage aaibaarheidsfactor. De term werd ca. 1969 gelanceerd door Rudy Kousbroek (alhoewel het tijdschrift <I>Gezin en Samenleving</I> er volgens een briefschrijver al een jaar eerder gewag van maakte!), maar sloeg pas echt aan in de jaren tachtig. Hij werd o.a. gebruikt bij de introductie van de Renault Twingo. Hierna werden ook samenstellingen met <I>-factor</I> als tweede lid, erg populair. Zo werd in <I>Cosmopolitan</I> (maart 1993) een nieuwe auto aangeprezen met de slogan ‘Kies voor de hoogste flirtfactor’. Elders werden samenstellingen aangetroffen als <I>bespreekbaarheidsfactor</I>, <I>lulligheidsfactor</I>, <I>troetelfactor</I>.</P><BLOCKQUOTE><I>Zijn tweede vrouw had een lagere aaibaarheidsfactor maar een veel grotere ver

In [8]:
# sluit de db af
db.close()

In [10]:
# import it into pandas

import pandas as pd
import numpy as np

decosterdf= pd.DataFrame(all_rows , columns=['ingang', 'lemmatekst'])
print(decosterdf.shape)
decosterdf.head()

(10281, 2)


ingang                                         lemmatekst
0        aaibaarheidsfactor  <P><B>aaibaarheidsfactor,</B> schertsende bena...
1           aandachtsgebied  <P><B>aandachtsgebied, -veld,</B> zaak, onderw...
2         aangeschoten wild  <P><B>aangeschoten wild,</B> voornamelijk in d...
3                  ankeiler  <P><B>a(a)nkeiler</B> (← Dui. <I>ankeilen</I> ...
4  iemand op iets aankijken  <P><B>aankijken: iemand op iets —,</B> iemand ...

# Even wat textmining 

* we halen het "lemma" uit de lemmatekst

In [15]:
from bs4 import BeautifulSoup

test= decosterdf.lemmatekst.iloc[0]
print(decosterdf.lemmatekst.iloc[0])
soup=BeautifulSoup(test,'lxml')
soup.find('q') 

<P><B>aaibaarheidsfactor,</B> schertsende benaming voor de mate van genoegen ondervonden door het aaien, knuffelen of vleien van bepaalde huisdieren (vooral katten), en bij uitbreiding ook mensen en dingen. Een alligator heeft een erg lage aaibaarheidsfactor. De term werd ca. 1969 gelanceerd door Rudy Kousbroek (alhoewel het tijdschrift <I>Gezin en Samenleving</I> er volgens een briefschrijver al een jaar eerder gewag van maakte!), maar sloeg pas echt aan in de jaren tachtig. Hij werd o.a. gebruikt bij de introductie van de Renault Twingo. Hierna werden ook samenstellingen met <I>-factor</I> als tweede lid, erg populair. Zo werd in <I>Cosmopolitan</I> (maart 1993) een nieuwe auto aangeprezen met de slogan ‘Kies voor de hoogste flirtfactor’. Elders werden samenstellingen aangetroffen als <I>bespreekbaarheidsfactor</I>, <I>lulligheidsfactor</I>, <I>troetelfactor</I>.</P><BLOCKQUOTE><I>Zijn tweede vrouw had een lagere aaibaarheidsfactor maar een veel grotere versmeltingsdrang. (Kees Van K

In [13]:
def pak_de_b(s):
    b= BeautifulSoup(s).find('b')
    if b:
        return b.string
    else:
        return np.nan

#test
pak_de_b(test)

'aaibaarheidsfactor,'

In [14]:
decosterdf['ingang_alfabetisch']= decosterdf.lemmatekst.apply(pak_de_b)
decosterdf.head(10)

ingang  \
0        aaibaarheidsfactor   
1           aandachtsgebied   
2         aangeschoten wild   
3                  ankeiler   
4  iemand op iets aankijken   
5             aanleunwoning   
6                 aanloggen   
7            aanloopcentrum   
8           aanpassingsklas   
9            aanrijding met   

                                          lemmatekst  \
0  <P><B>aaibaarheidsfactor,</B> schertsende bena...   
1  <P><B>aandachtsgebied, -veld,</B> zaak, onderw...   
2  <P><B>aangeschoten wild,</B> voornamelijk in d...   
3  <P><B>a(a)nkeiler</B> (← Dui. <I>ankeilen</I> ...   
4  <P><B>aankijken: iemand op iets —,</B> iemand ...   
5  <P><B>aanleunwoning,</B> bejaardenflat of woni...   
6  <P><B>aanloggen,</B> een verbinding maken met ...   
7  <P><B>aanloopcentrum, -punt,</B> centrum, plaa...   
8  <P><B>aanpassingsklas,</B> in Vlaanderen: klas...   
9  <P><B>aanrijding met; — zonder,</B> bij de pol...   

             ingang_alfabetisch  
0           aaibaarheidsfactor,  
1       aandachtsgebied, -veld,  
2            aangeschoten wild,  
3                   a(a)nkeiler  
4  aankijken: iemand op iets —,  
5                aanleunwoning,  
6                    aanloggen,  
7        aanloopcentrum, -punt,  
8              aanpassingsklas,  
9     aanrijding met; — zonder,